## Visualize word2vec embeddings in tensorboard

In [1]:
import tensorflow as tf
from tensorflow.contrib.tensorboard.plugins import projector
import numpy as np
import gensim

# import warnings
# warnings.filterwarnings(action='ignore', category=UserWarning, module='gensim')

### Train a small word2vec model

In [2]:
text_file_name = 'wikipedia_small/wikipedia.txt'

sentences = gensim.models.word2vec.LineSentence(text_file_name, limit=100000)

model = gensim.models.Word2Vec(sentences, size=10, window=5, min_count=5, workers=4)


In [3]:
max_size = len(model.wv.vocab)-1

In [ ]:
w2v = np.zeros((max_size,model.layer1_size))

In [ ]:
w2v

In [ ]:
with open("metadata.tsv", 'wb') as file_metadata:
    for i,word in enumerate(model.wv.index2word[:max_size]):
        w2v[i] = model.wv[word]
        file_metadata.write(word.encode('utf8') + '\n')        

In [ ]:
w2v

In [ ]:
sess = tf.InteractiveSession()

In [ ]:
#Let us create a 2D tensor called embedding that holds our embeddings.
with tf.device("/cpu:0"):
    embedding = tf.Variable(w2v, trainable=False, name='embedding')


In [ ]:
tf.global_variables_initializer().run()

In [ ]:
path = 'tensorboard'

In [ ]:
# let us create an object to Saver class which is actually used to 
#save and restore variables to and from our checkpoints
saver = tf.train.Saver()

In [ ]:
# using file writer, we can save our summaries and events to our event file.
writer = tf.summary.FileWriter(path, sess.graph)

In [ ]:
# adding into projector
config = projector.ProjectorConfig()
embed = config.embeddings.add()
embed.tensor_name = 'embedding'
embed.metadata_path = 'metadata.tsv'

In [ ]:
# Specify the width and height of a single thumbnail.
projector.visualize_embeddings(writer, config)

saver.save(sess, path+'/model.ckpt', global_step=max_size)